In [8]:
import pandas as pd
import numpy as np
import openpyxl
import os
from pathlib import Path
from openpyxl import load_workbook
import re

print("✓ pandas version:", pd.__version__)
print("✓ numpy version:", np.__version__)
print("✓ openpyxl version:", openpyxl.__version__)
print("\n¡Todas las librerías están instaladas correctamente!")

ARCHIVO_ORIGEN = r"D:\Mateo\ICSI\Proyecto\Data\Raw\Poblacion\Data\Inputs\Censo\censo_pob_sexo_edades_quin_2017.xlsx"
AÑO_CENSO = 2017
df = pd.read_excel(ARCHIVO_ORIGEN, header=None) # Lee sin encabezados para procesar manualmente

def procesar_censo_estructura_real(df):
    """
    Procesa el censo basado en la estructura real mostrada.
    """
    datos_procesados = []
    area_actual = {"ubigeo": "", "departamento": "", "provincia": "", "distrito": ""}
    
    # Renombra las columnas para facilitar la indexación
    df = df.reset_index(drop=True)
    df.columns = [str(i) for i in range(len(df.columns))]
    
    print("=== INICIANDO PROCESAMIENTO DEL ARCHIVO ===")
    
    for i in range(len(df)):
        fila = df.iloc[i]
        
        # 1. Buscar área geográfica
        if (pd.notna(fila.get('1', None)) and 'AREA' in str(fila['1']) and
            pd.notna(fila.get('2', None)) and any(provincia in str(fila['2']) for provincia in ['Amazonas', 'Áncash', 'Apurímac', 'Arequipa', 'Ayacucho', 'Cajamarca', 'Callao', 'Cusco', 'Huancavelica', 'Huánuco', 'Ica', 'Junín', 'La Libertad', 'Lambayeque', 'Lima', 'Loreto', 'Madre de Dios', 'Moquegua', 'Pasco', 'Piura', 'Puno', 'San Martín', 'Tacna', 'Tumbes', 'Ucayali'])):
            
            print(f"✅ ÁREA encontrada en fila {i}: {fila['1']} | {fila['2']}")
            
            try:
                ubigeo_match = re.search(r'(\d{6})', str(fila['1']))
                area_actual['ubigeo'] = ubigeo_match.group(1) if ubigeo_match else ""
                
                geo_texto = str(fila['2']).strip()
                partes = [p.strip() for p in geo_texto.split(',')]
                
                area_actual['departamento'] = partes[0] if len(partes) >= 1 else ''
                area_actual['provincia'] = partes[1] if len(partes) >= 2 else ''
                if len(partes) >= 3:
                    distrito_texto = re.sub(r'distrito:\s*', '', partes[2], flags=re.IGNORECASE)
                    area_actual['distrito'] = distrito_texto.strip()
            except Exception as e:
                print(f"❌ Error al procesar área en fila {i}: {e}. Fila: {fila.to_dict()}")
            
            print(f"   Datos geográficos actualizados: {area_actual}")
            continue

        # 2. Buscar encabezados de tabla de datos
        if (pd.notna(fila.get('1', None)) and 'P: Edad' in str(fila['1']) and
            pd.notna(fila.get('2', None)) and 'P: Sexo' in str(fila['2'])):
            
            print(f"✅ ENCABEZADOS de tabla en fila {i}")
            
            if i + 1 < len(df):
                fila_encabezados = df.iloc[i + 1]
                
                if (pd.notna(fila_encabezados.get('2', None)) and 'Hombre' in str(fila_encabezados['2']) and
                    pd.notna(fila_encabezados.get('3', None)) and 'Mujer' in str(fila_encabezados['3']) and
                    pd.notna(fila_encabezados.get('4', None)) and 'Total' in str(fila_encabezados['4'])):
                    
                    print(f"✅ ENCABEZADOS de sexo en fila {i+1}")
                    
                    for j in range(i + 2, len(df)):
                        fila_datos = df.iloc[j]
                        
                        # Condición de salida del bucle de datos
                        if pd.notna(fila_datos.get('1', None)) and 'AREA' in str(fila_datos['1']):
                            print("⚡ Nueva área encontrada, terminando bloque de datos.")
                            break
                        
                        # Ignorar filas vacías
                        if pd.isna(fila_datos.get('1', None)) or str(fila_datos.get('1', '')).strip() == '':
                            continue
                            
                        # Procesar filas de datos de edad
                        if (pd.notna(fila_datos.get('1', None)) and 
                            'De' in str(fila_datos['1']) and 'años' in str(fila_datos['1'])):
                            
                            grupo_edad = str(fila_datos['1']).strip()
                            print(f"📊 Procesando grupo de edad: {grupo_edad}")
                            
                            for col_idx, sexo in [(2, 'Hombre'), (3, 'Mujer'), (4, 'Total')]:
                                try:
                                    valor = fila_datos[str(col_idx)]
                                    valor_limpio = re.sub(r'[^\d]', '', str(valor))
                                    if valor_limpio:
                                        valor_num = float(valor_limpio)
                                        
                                        datos_procesados.append({
                                            'Ubigeo': area_actual['ubigeo'],
                                            'Departamento': area_actual['departamento'],
                                            'Provincia': area_actual['provincia'],
                                            'Distrito': area_actual['distrito'],
                                            'grupo_edad': grupo_edad,
                                            'sexo': sexo,
                                            'valor': valor_num,
                                            'Anio': AÑO_CENSO
                                        })
                                except Exception as e:
                                    print(f"   ❌ Error al procesar valor en fila {j}, col {col_idx}: {e}")
                        
                        # Si encuentra "Total" final
                        elif (pd.notna(fila_datos.get('1', None)) and 'Total' in str(fila_datos['1']) and 
                            not any(x in str(fila_datos['1']) for x in ['De', 'años'])):
                            print("📈 Total general encontrado, terminando bloque.")
                            break
            
        else:
            # Mensaje de depuración para filas que no coinciden con los patrones
            valores_fila = fila.iloc[:6].tolist() if len(fila) > 5 else fila.tolist()
            valores_fila_str = [str(v)[:30] if pd.notna(v) else 'NaN' for v in valores_fila]
            print(f"➡️ Fila {i} no coincide con ningún patrón. Contenido: {valores_fila_str}")
            
    # Crear DataFrame final
    df_final = pd.DataFrame(datos_procesados)
    
    if not df_final.empty:
        print(f"🎉 PROCESAMIENTO EXITOSO: {len(df_final)} registros")
        df_final['valor'] = pd.to_numeric(df_final['valor'], errors='coerce')
        df_final = df_final.dropna(subset=['valor'])
    else:
        print("❌ NO SE ENCONTRARON DATOS VÁLIDOS")
        
    return df_final

# Ejecutar el procesamiento
df_final = procesar_censo_estructura_real(df)

if not df_final.empty:
    print("\n=== RESULTADO FINAL ===")
    print(f"Total de registros: {len(df_final)}")
    print("\nPrimeros 5 registros:")
    print(df_final.head())
else:
    print("El DataFrame final está vacío. Revisa la salida de la depuración para encontrar el error.")

df_final['grupo_edad'] = df_final['grupo_edad'].str.strip() 
df_final['sexo'] = df_final['sexo'].str.strip() 
 


import os
ruta_destino = r"D:\Mateo\ICSI\Proyecto\Data\Raw\Poblacion\Data\Processing"
nombre_archivo = "pob_censo_edades_sexo_2017.csv"
ruta_completa = os.path.join(ruta_destino, nombre_archivo)
df_final.to_csv(ruta_completa, index=False, encoding='latin1')


✓ pandas version: 2.3.1
✓ numpy version: 2.3.1
✓ openpyxl version: 3.1.5

¡Todas las librerías están instaladas correctamente!
=== INICIANDO PROCESAMIENTO DEL ARCHIVO ===
➡️ Fila 0 no coincide con ningún patrón. Contenido: ['Título', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 1 no coincide con ningún patrón. Contenido: ['vvv', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 2 no coincide con ningún patrón. Contenido: ['Área Geográfica', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 3 no coincide con ningún patrón. Contenido: ['Toda la Base de Datos', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 4 no coincide con ningún patrón. Contenido: ['Crosstab', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 5 no coincide con ningún patrón. Contenido: ['  de P: Edad en grupos quinque', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 6 no coincide con ningún patrón. Contenido: ['  por P: Sexo', 'NaN', 'NaN', 'NaN', 'NaN']
➡️ Fila 7 no coincide con ningún patrón. Contenido: ['NaN', 'NaN', 'NaN', 'NaN', 'NaN']
✅ ÁREA encontrada en fila 8: AREA # 010101 | Amazo